In [1]:
import sys
import pandas as pd
import dateutil
import numpy as np
from sklearn.model_selection import LeaveOneGroupOut

import tensorflow as tf
from keras.callbacks import EarlyStopping
from keras.callbacks import ModelCheckpoint
from keras.models import load_model
tf.config.experimental_run_functions_eagerly(True)

sys.path.append('../')
from utilities.ANN_functions import root_mean_squared_error, r2_keras_loss, r2_keras
from utilities.ANN_functions import create_loso_model, create_loyo_model, create_lsyso_model

import warnings
warnings.filterwarnings('ignore')
date_parser = lambda x: dateutil.parser.parse(x, ignoretz=True)

from dask.distributed import Client
client = Client()
#client = Client(n_workers=2, threads_per_worker=1, memory_limit='1GB')
client

Instructions for updating:
Use `tf.config.run_functions_eagerly` instead of the experimental version.


<Client: 'tcp://127.0.0.1:46221' processes=8 threads=32, memory=31.27 GiB>

In [2]:
cs_file = '../data/SMB_input_2011_2015.csv'

df = pd.read_csv(cs_file,
   delimiter='\t', index_col=['Date/Time'],
    parse_dates=['Date/Time'], na_values='NAN',date_parser=date_parser)

In [3]:
X = (df.drop(['Diff', 'Event'], axis=1)).to_numpy()
y = (df['Diff'].copy()).to_numpy()

In [4]:
loso = LeaveOneGroupOut()
groups = df['Event'].values

In [5]:
x, n_features = X.shape

In [6]:
path_ann = '../ANN/LOSO/CV/'

In [7]:
def run_loso():
    # Leave-One-Stake-Out
    i = 1
    test_rmse = []
    for train_index, test_index in loso.split(X, y, groups):
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]
        model = create_loso_model(n_features, final=False)
        es = EarlyStopping(monitor='val_loss', mode='min', min_delta=0.01, patience=1000)
        mc = ModelCheckpoint(path_ann + 'stake_'+str(i)+'_model.h5', monitor='val_loss', mode='min',
                             save_best_only=True, verbose=1)

        history = model.fit(X_train, y_train, validation_data = (X_test, y_test), 
                            epochs=2000, batch_size = 11, verbose=1, callbacks=[es, mc])

        best_model = load_model(path_ann  + 'stake_'+str(i)+'_model.h5',
                                custom_objects={"r2_keras": r2_keras, 
                                                "r2_keras_loss": r2_keras_loss, 
                                                "root_mean_squared_error": root_mean_squared_error})

        score = best_model.evaluate(X_test, y_test)

        test_rmse.append(score[0])

        i= i+1

In [ ]:
#client.submit(run_loso)

In [ ]:
print(test_rmse)

In [8]:
df['Year'] = df.index.year

In [9]:
loyo = LeaveOneGroupOut()
groups = df['Year'].values

In [10]:
X = (df.drop(['Diff', 'Event', 'Year'], axis=1)).to_numpy()
y = (df['Diff'].copy()).to_numpy()

In [11]:
x, n_features = X.shape

In [12]:
path_ann = '../ANN/LOYO/CV/'

In [13]:
def run_loyo():
    # Leave-One-Year-Out
    i = 1
    test_rmse = []
    for train_index, test_index in loyo.split(X, y, groups):
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]
        model = create_loyo_model(n_features)
        es = EarlyStopping(monitor='val_loss', mode='min', min_delta=0.01, patience=1000)
        mc = ModelCheckpoint(path_ann + 'year_'+str(i)+'_model.h5', monitor='val_loss', mode='min',
                             save_best_only=True, verbose=1)

        history = model.fit(X_train, y_train, validation_data = (X_test, y_test), 
                            epochs=2000, batch_size = 5, verbose=1, callbacks=[es, mc])

        best_model = load_model(path_ann  + 'year_'+str(i)+'_model.h5',
                                custom_objects={"r2_keras": r2_keras, 
                                                "r2_keras_loss": r2_keras_loss, 
                                                "root_mean_squared_error": root_mean_squared_error})

        score = best_model.evaluate(X_test, y_test)

        test_rmse.append(score[0])
        i= i+1

In [14]:
client.submit(run_loyo)

<Future: pending, key: run_loyo-8ace052cfd6da507ae1ce4ede04b26e3>

2022-07-12 10:56:26.947821: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
/home/isadora/miniconda3/envs/dl_glacier/lib/python3.10/site-packages/keras/optimizer_v2/rmsprop.py:130: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(RMSprop, self).__init__(name, **kwargs)


Epoch 1/2000
182/206 [=========================>....] - ETA: 0s - loss: 0.2598 - root_mean_squared_error: 0.2598
Epoch 1: val_loss improved from inf to 7.80663, saving model to ../ANN/LOYO/CV/year_1_model.h5
206/206 [==============================] - 1s 2ms/step - loss: 0.2529 - root_mean_squared_error: 0.2547 - val_loss: 7.8066 - val_root_mean_squared_error: 7.7989
Epoch 2/2000
193/206 [===========================>..] - ETA: 0s - loss: 0.1995 - root_mean_squared_error: 0.1995
Epoch 2: val_loss improved from 7.80663 to 1.01980, saving model to ../ANN/LOYO/CV/year_1_model.h5
206/206 [==============================] - 0s 1ms/step - loss: 0.2011 - root_mean_squared_error: 0.2011 - val_loss: 1.0198 - val_root_mean_squared_error: 1.0145
Epoch 3/2000
195/206 [===========================>..] - ETA: 0s - loss: 0.1985 - root_mean_squared_error: 0.1985
Epoch 3: val_loss improved from 1.01980 to 0.90151, saving model to ../ANN/LOYO/CV/year_1_model.h5
206/206 [==============================] - 0s 

In [16]:
#print(test_rmse)

In [17]:
X = (df.drop(['Diff', 'Event', 'Year'], axis=1)).to_numpy()
y = (df['Diff'].copy()).to_numpy()

In [18]:
groups = df['Event'].values
years = df.drop_duplicates(subset=['Year'])['Year'].values

In [19]:
x, n_features = X.shape

In [20]:
path_ann = '../ANN/LOYSO/CV/'

In [22]:
def run_loyso():
    # Leave-One-Year-Stake-Out
    i = 1 
    test_rmse = []
    for year, (train_index, test_index) in zip(years, loso.split(X, y, groups)):
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]
        model = create_lsyso_model(n_features, final=False)
        es = EarlyStopping(monitor='val_loss', mode='min', min_delta=0.01, patience=1000)
        mc = ModelCheckpoint(path_ann + 'year_stake_'+str(i)+'_model.h5', monitor='val_loss', mode='min',
                             save_best_only=True, verbose=1)

        history = model.fit(X_train, y_train, validation_data = (X_test, y_test), 
                            epochs=2000, batch_size = 5, verbose=1, callbacks=[es, mc])

        best_model = load_model(path_ann  + 'year_stake_'+str(i)+'_model.h5',
                                custom_objects={"r2_keras": r2_keras, 
                                                "r2_keras_loss": r2_keras_loss, 
                                                "root_mean_squared_error": root_mean_squared_error})

        score = best_model.evaluate(X_test, y_test)

        test_rmse.append(score[0])
        i= i+1
    return test_rmse

In [23]:
x = client.submit(run_loyso)

2022-07-12 11:19:25.122670: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
/home/isadora/miniconda3/envs/dl_glacier/lib/python3.10/site-packages/keras/optimizer_v2/rmsprop.py:130: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(RMSprop, self).__init__(name, **kwargs)


Epoch 1/2000
162/192 [========================>.....] - ETA: 0s - loss: 0.3092 - root_mean_squared_error: 0.3092
Epoch 1: val_loss improved from inf to 0.17808, saving model to ../ANN/LOYSO/CV/year_stake_1_model.h5
192/192 [==============================] - 1s 2ms/step - loss: 0.2945 - root_mean_squared_error: 0.2943 - val_loss: 0.1781 - val_root_mean_squared_error: 0.1746
Epoch 2/2000
174/192 [==========================>...] - ETA: 0s - loss: 0.2298 - root_mean_squared_error: 0.2298
Epoch 2: val_loss improved from 0.17808 to 0.17588, saving model to ../ANN/LOYSO/CV/year_stake_1_model.h5
192/192 [==============================] - 0s 1ms/step - loss: 0.2379 - root_mean_squared_error: 0.2379 - val_loss: 0.1759 - val_root_mean_squared_error: 0.1726
Epoch 3/2000
168/192 [=========================>....] - ETA: 0s - loss: 0.2281 - root_mean_squared_error: 0.2281
Epoch 3: val_loss did not improve from 0.17588
192/192 [==============================] - 0s 1ms/step - loss: 0.2312 - root_mean_sq

In [24]:
print(x.result())

[0.16657757759094238, 0.14947865903377533, 0.1260359287261963, 0.1752920299768448, 0.18699714541435242]
